# INTRODUCTION: Gourmet Bussines

A chef has contacted me, since he needs to do a study of the businesses that have been successful in the culinary field he develops.

With respect to his experience, he has been based on Gourmet businesses in certain areas of Mexico City where they have been well received by the population.

His intention is to open a gourmet-type business in a potential place for his success and where the concept has not yet arrived.

The proposal that he makes to me is the following:

## Customer's proposal

Dear Minerva:
I am in contact with you to formally make my intention to require your artificial intelligence / machine learning service, for which I will detail below the requirements of the project you will develop.

Approach

As part of a professional growth, I intend to open a gourmet store, which will have as main selling axes:

Butchery: National and imported cuts of beef (prime quality) will be sold, wagyu meat (imported from Japan), aged meat (inside the store by us in aging chambers), pork cuts, piglets, exotic meats such as wild boar, crocodile.
Fish and seafood: Daily selection attached to sustainable fishing, fish and shellfish national and imported.
Spices, fruits, vegetables and other items related to gourmet preparations.
Workshops, courses.

Location

As part of the support I require from you, I need to determine the ideal location of the store, which could be in the Cuahutemoc or Benito Juarez delegation, for which I need to consider the following points in order to make a decision:

Purchase incidence: Take into account the purchasing trends of customers, according to nearby businesses.
Opening hours and closing of the store.
Market segmentation.

Taking these points into account, I ask for your expertise to be able to create a model and suitable with the needs that I have.

Without further ado, I remain attentive to your response.

# DATA

We will rely on Foursquare to have the necessary information of the places, as well as their popularity and the business line that is of interest.

In order to locate each of the colonies in the determined areas of Mexico City, we will access the INEGI portal, which is the National Institute of Statistics and Geography of Mexico, through a web query, we can download a csv file with the geographic coordinates of all the neighborhoods of the City and to be able to work on these data.

In the question of the procedure, we can highlight the places of Gourmet turnaround related to the interest of my client and associate the types of businesses and sites that exist around it, in order to associate a set of behavior related to the gourmet sector and thus be able to extrapolate this set to a new town in the city

## csv File filter and Downloaded from https://www.inegi.org.mx/app/geo2/cng/

<h2>Import dependencies that we will need</h2>

In [2]:
import pandas as pd
import numpy as np

In [3]:
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

#!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

#!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

print('Libraries imported.')

Libraries imported.


Preview of the Data obtained

In [4]:
geo=pd.read_csv('borough_data.csv')
geo.columns = [c.replace(' ', '_') for c in geo.columns]
geo.rename(index=str, columns={'Nombre_de_municipio': 'Borough','Nombre_geografico':'Neighborhood','Lat_dec':'Latitude','Lon_dec':'Longitude'}, inplace=True)
geo.head()

Neighborhood  Nombre_conocido      Clase Termino_generico  \
0       10 de Abril              NaN  Localidad          Colonia   
1        10 de Mayo              NaN  Localidad          Colonia   
2   12 de Diciembre              NaN  Localidad          Colonia   
3      15 de Agosto              NaN  Localidad          Colonia   
4  16 de Septiembre              NaN  Localidad          Colonia   

   Clave_de_entidad Nombre_de_entidad  Clave_de_municipio  \
0                 9  Ciudad de Mexico                  16   
1                 9  Ciudad de Mexico                  17   
2                 9  Ciudad de Mexico                   7   
3                 9  Ciudad de Mexico                   5   
4                 9  Ciudad de Mexico                  16   

               Borough  Clave_de_localidad  Nombre_de_localidad       Latitud  \
0       Miguel Hidalgo                   1       Miguel Hidalgo  19°26'55'' N   
1  Venustiano Carranza                   1  Venustiano Carranza  19°26'01'' N   
2           Iztapalapa                   1           Iztapalapa  19°19'45'' N   
3    Gustavo A. Madero                   1    Gustavo A. Madero  19°29'05'' N   
4       Miguel Hidalgo                   1       Miguel Hidalgo  19°24'07'' N   

       Longitud   Latitude  Longitude  
0  99°12'30'' W  19.448611  99.208333  
1  99°07'05'' W  19.433611  99.118056  
2  99°06'02'' W  19.329167  99.100556  
3  99°06'23'' W  19.484722  99.106389  
4  99°12'25'' W  19.401944  99.206944

### Filter the DataFrame with the data of Borough,Neighborhood,Latitude and Longitude

In [5]:
df = pd.DataFrame()
df['Borough']=geo.Borough
df['Neighborhood']=geo.Neighborhood
df['Latitude']=geo.Latitude
###multiply longitud by -1 in order to use in Foursquare
df['Longitude']=(geo.Longitude)*-1
df.head()

Borough      Neighborhood   Latitude  Longitude
0       Miguel Hidalgo       10 de Abril  19.448611 -99.208333
1  Venustiano Carranza        10 de Mayo  19.433611 -99.118056
2           Iztapalapa   12 de Diciembre  19.329167 -99.100556
3    Gustavo A. Madero      15 de Agosto  19.484722 -99.106389
4       Miguel Hidalgo  16 de Septiembre  19.401944 -99.206944

#### Use geopy library to get the latitude and longitude values of Mexico City.

In [6]:
address = 'Mexico City, MX'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Mexico City are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Mexico City are 19.4326009, -99.1333416.


#### Create a map of Mexico City with neighborhoods superimposed on top.

In [7]:
# create map of Mexico using latitude and longitude values
map_mx = folium.Map(location=[latitude, longitude], zoom_start=11.48)

# add markers to map
for lat, lng, borough, Neighborhood in zip(df['Latitude'], df['Longitude'], df['Borough'], df['Neighborhood']):
    label = '{}, {}'.format(Neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_mx)  
map_mx

# Methodology 

The main component of analysis in this study is by means of the Foursqare search tool.

Through this tool we will obtain the necessary information about the most visited venues in Mexico City.

### Dimension of the Data.
The 16 Delegations or Boroughs that make up Mexico City have a number of neighborhoods, the list of these neighborhoods and their coordinates are obtained through the INEGI database mentioned in the previous section.

Therefore, when downloading said database, we obtain that in Mexico City there are 1232 neighborhoods.

Due to the immense number of neighborhoods, and therefore the queries of the neighborhood venues that will be on Foursquare exceeds the allowed number of daily consultations and customer requirements, We will analyze the main Boroughs that are Miguel Hidalgo and Cuauhtemoc to base our study

These Boroughs are the most representative of the restaurant sector of the city.

For this reason, my client wants this to be the area in which the behavior of the target businesses (Safood, Gourmet, Aged meat) is analyzed with respect to the most visited places in this area.

## We want to know the Venues of two specific Boroughs : Miguel Hidalgo and Cuauhtemoc

In [8]:
df_mig = df.loc[(df['Borough'] == 'Miguel Hidalgo')]# & (df['Borough'] == 'Cuauhtemoc')]
df_cuau= df.loc[(df['Borough'] == 'Cuauhtemoc')]
print(df_cuau.count())
print(df_mig.count())

Borough         33
Neighborhood    33
Latitude        33
Longitude       33
dtype: int64
Borough         81
Neighborhood    81
Latitude        81
Longitude       81
dtype: int64


#### Define Foursquare Credentials and Version

In [9]:
CLIENT_ID = 'XDYF0514VQMWG3DPCZLR2SRXJLCGCXJS5EHJ22QRC5XJWXJJ' # your Foursquare ID
CLIENT_SECRET = 'Q3C5ZY4PRPBBKTLOQI2Z2P4U5KGS3C1CH5B1LT3B1MKVVVKI' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

LIMIT = 100


### Explore Neighborhoods in Mexico City

In [10]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

### Get Near Venues in Mexico City

In [11]:
mx_venues = getNearbyVenues(names=df_cuau['Neighborhood'],
                                   latitudes=df_cuau['Latitude'],
                                   longitudes=df_cuau['Longitude']
                                  )

mx_venues.head()

Algarin
Ampliacion Asturias
Asturias
Atlampa
Buenavista
Buenos Aires
Centro
Condesa
Cuauhtemoc
Doctores
Esperanza
Ex-Hipodromo de Peralvillo
Felipe Pescador
Guerrero
Hipodromo
Hipodromo Condesa
Juarez
Maza
Morelos
Nonoalco Tlatelolco
Obrera
Paulino Navarro
Peralvillo
Roma Norte
Roma Sur
San Rafael
San Simon Tolnahuac
Santa Maria Insurgentes
Santa Maria la Ribera
Tabacalera
Transito
Valle Gomez
Vista Alegre


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0      Algarin              19.405833              -99.140556   
1      Algarin              19.405833              -99.140556   
2      Algarin              19.405833              -99.140556   
3      Algarin              19.405833              -99.140556   
4      Algarin              19.405833              -99.140556   

                  Venue  Venue Latitude  Venue Longitude      Venue Category  
0     Barbacoa El Profe       19.407052       -99.139187  Mexican Restaurant  
1           Los Tolucos       19.406723       -99.142527  Mexican Restaurant  
2          Los Pollitos       19.405406       -99.142848  Mexican Restaurant  
3       Harley-Davidson       19.406162       -99.142319     Motorcycle Shop  
4  Barbacoa Los Marinos       19.405346       -99.142419          Taco Place

### Let's check how many venues were returned for each neighborhood

In [12]:
df_filt=pd.DataFrame(mx_venues.groupby('Neighborhood').count())
best_N = df_filt.loc[df_filt['Venue'].values==100].index.values
best_1=mx_venues.loc[mx_venues['Neighborhood'].isin(best_N)]
best_1


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
154              Centro              19.433056              -99.137500   
155              Centro              19.433056              -99.137500   
156              Centro              19.433056              -99.137500   
157              Centro              19.433056              -99.137500   
158              Centro              19.433056              -99.137500   
159              Centro              19.433056              -99.137500   
160              Centro              19.433056              -99.137500   
161              Centro              19.433056              -99.137500   
162              Centro              19.433056              -99.137500   
163              Centro              19.433056              -99.137500   
164              Centro              19.433056              -99.137500   
165              Centro              19.433056              -99.137500   
166              Centro              19.433056              -99.137500   
167              Centro              19.433056              -99.137500   
168              Centro              19.433056              -99.137500   
169              Centro              19.433056              -99.137500   
170              Centro              19.433056              -99.137500   
171              Centro              19.433056              -99.137500   
172              Centro              19.433056              -99.137500   
173              Centro              19.433056              -99.137500   
174              Centro              19.433056              -99.137500   
175              Centro              19.433056              -99.137500   
176              Centro              19.433056              -99.137500   
177              Centro              19.433056              -99.137500   
178              Centro              19.433056              -99.137500   
179              Centro              19.433056              -99.137500   
180              Centro              19.433056              -99.137500   
181              Centro              19.433056              -99.137500   
182              Centro              19.433056              -99.137500   
183              Centro              19.433056              -99.137500   
184              Centro              19.433056              -99.137500   
185              Centro              19.433056              -99.137500   
186              Centro              19.433056              -99.137500   
187              Centro              19.433056              -99.137500   
188              Centro              19.433056              -99.137500   
189              Centro              19.433056              -99.137500   
190              Centro              19.433056              -99.137500   
191              Centro              19.433056              -99.137500   
192              Centro              19.433056              -99.137500   
193              Centro              19.433056              -99.137500   
194              Centro              19.433056              -99.137500   
195              Centro              19.433056              -99.137500   
196              Centro              19.433056              -99.137500   
197              Centro              19.433056              -99.137500   
198              Centro              19.433056              -99.137500   
199              Centro              19.433056              -99.137500   
200              Centro              19.433056              -99.137500   
201              Centro              19.433056              -99.137500   
202              Centro              19.433056              -99.137500   
203              Centro              19.433056              -99.137500   
204              Centro              19.433056              -99.137500   
205              Centro              19.433056              -99.137500   
206              Centro              19.433056              -99.137500   
207            

##  Analyze Each Neighborhood

In [13]:
# one hot encoding
mx_onehot = pd.get_dummies(best_1[['Venue Category']], prefix="", prefix_sep="")
# add neighborhood column back to dataframe
mx_onehot['Neighborhood'] = best_1['Neighborhood'] 
# move neighborhood column to the first column
mx_onehot = mx_onehot.set_index('Neighborhood').reset_index()
# create the fixed columns
fixed_columns = [mx_onehot.columns[0]] + mx_onehot.columns[1:].values.tolist() 
mx_onehot = mx_onehot[fixed_columns]
mx_onehot.head()


Neighborhood  American Restaurant  Antique Shop  Argentinian Restaurant  \
0       Centro                    0             0                       0   
1       Centro                    0             0                       0   
2       Centro                    0             0                       0   
3       Centro                    0             0                       0   
4       Centro                    0             0                       0   

   Art Gallery  Art Museum  Arts & Crafts Store  Asian Restaurant  \
0            0           0                    0                 0   
1            0           1                    0                 0   
2            0           0                    0                 0   
3            0           0                    0                 0   
4            0           0                    0                 0   

   Athletics & Sports  BBQ Joint  Bakery  Bar  Bed & Breakfast  Beer Bar  \
0                   0          0       0    0                0         0   
1                   0          0       0    0                0         0   
2                   0          0       0    0                0         0   
3                   0          0       0    0                0         0   
4                   0          0       0    0                0         0   

   Beer Garden  Beer Store  Belgian Restaurant  Bike Rental / Bike Share  \
0            0           0                   0                         0   
1            0           0                   0                         0   
2            0           0                   0                         0   
3            0           0                   0                         0   
4            0           0                   0                         0   

   Bike Trail  Bistro  Board Shop  Bookstore  Boutique  Boxing Gym  \
0           0       0           0          0         0           0   
1           0       0           0          0         0           0   
2           0       0           0          0         0           0   
3           0       0           0          0         0           0   
4           0       0           0          0         0           0   

   Breakfast Spot  Brewery  Bubble Tea Shop  Building  Burger Joint  \
0               0        0                0         0             0   
1               0        0                0         0             0   
2               0        0                0         0             0   
3               0        0                0         0             0   
4               0        0                0         0             0   

   Burrito Place  Cafeteria  Café  Camera Store  Candy Store  Cheese Shop  \
0              0          0     0             0            0            0   
1              0          0     0             0            0            0   
2              0          0     0             0            0            0   
3              0          0     0             0            0            0   
4              0          0     0             0            0            0   

   Chinese Restaurant  Chocolate Shop  Clothing Store  Cocktail Bar  \
0                   0               0               0             0   
1                   0               0               0             0   
2                   0               0               0             0   
3                   0               0               0             0   
4                   0               0               0             0   

   Coffee Shop  College Auditorium  Comfort Food Restaurant  Cosmetics Shop  \
0            0                   0                        0               0   
1            0                   0                        0               0   
2            0                   0                        0               0   
3            0                   0                        0               0   
4            0                   0                        0               0  

#### Next, let's group rows by neighborhood and by taking the mean of the frequency of occurrence of each category

In [14]:
mx_grouped = mx_onehot.groupby('Neighborhood').mean().reset_index()
mx_grouped

Neighborhood  American Restaurant  Antique Shop  \
0             Centro                 0.00          0.00   
1            Condesa                 0.00          0.00   
2         Cuauhtemoc                 0.01          0.00   
3          Hipodromo                 0.00          0.01   
4  Hipodromo Condesa                 0.00          0.00   
5             Juarez                 0.01          0.00   
6         Roma Norte                 0.00          0.00   

   Argentinian Restaurant  Art Gallery  Art Museum  Arts & Crafts Store  \
0                    0.01         0.03        0.04                 0.02   
1                    0.02         0.01        0.00                 0.00   
2                    0.01         0.00        0.00                 0.00   
3                    0.03         0.00        0.00                 0.00   
4                    0.02         0.00        0.00                 0.00   
5                    0.02         0.04        0.00                 0.00   
6                    0.01         0.00        0.00                 0.02   

   Asian Restaurant  Athletics & Sports  BBQ Joint  Bakery   Bar  \
0              0.00                0.00       0.00    0.05  0.07   
1              0.00                0.01       0.00    0.03  0.02   
2              0.01                0.01       0.01    0.02  0.01   
3              0.00                0.00       0.01    0.01  0.03   
4              0.00                0.00       0.01    0.02  0.02   
5              0.00                0.00       0.01    0.03  0.02   
6              0.01                0.00       0.01    0.05  0.05   

   Bed & Breakfast  Beer Bar  Beer Garden  Beer Store  Belgian Restaurant  \
0             0.00      0.00         0.01        0.00                0.00   
1             0.00      0.01         0.00        0.00                0.00   
2             0.00      0.00         0.00        0.00                0.01   
3             0.02      0.00         0.00        0.00                0.00   
4             0.02      0.00         0.00        0.01                0.00   
5             0.01      0.00         0.00        0.00                0.00   
6             0.00      0.00         0.00        0.00                0.00   

   Bike Rental / Bike Share  Bike Trail  Bistro  Board Shop  Bookstore  \
0                      0.00        0.00    0.00        0.00       0.01   
1                      0.00        0.00    0.00        0.00       0.00   
2                      0.00        0.01    0.01        0.00       0.00   
3                      0.01        0.00    0.00        0.00       0.01   
4                      0.01        0.00    0.03        0.00       0.02   
5                      0.00        0.00    0.00        0.00       0.01   
6                      0.00        0.00    0.02        0.01       0.01   

   Boutique  Boxing Gym  Breakfast Spot  Brewery  Bubble Tea Shop  Building  \
0      0.03        0.00            0.00     0.02             0.00      0.01   
1      0.01        0.01            0.00     0.00             0.00      0.00   
2      0.00        0.00            0.00     0.01             0.00      0.00   
3      0.01        0.00            0.01     0.00             0.01      0.00   
4      0.00        0.00            0.01     0.00             0.00      0.00   
5      0.03        0.00            0.01     0.00             0.01      0.00   
6      0.05        0.00            0.00     0.00             0.00      0.00   

   Burger Joint  Burrito Place  Cafeteria  Café  Camera Store  Candy Store  \
0          0.00           0.00       0.00  0.04          0.00         0.01   
1          0.00           0.00       0.00  0.02          0.00         0.00   
2          0.00           0.00       0.00  0.06          0.00         0.01   
3          0.01           0.00       0.01  0.04          0.01         0.00   
4          0.03           0.00       0.01  0.03          0.00         0.00   
5          0.01           0.00       0.00  0.02          0.00         0.00   


#### Let's print each neighborhood along with the top 5 most common venues

In [15]:
num_top_venues = 5

for hood in mx_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = mx_grouped[mx_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Centro----
                venue  freq
0  Mexican Restaurant  0.10
1                 Bar  0.07
2              Bakery  0.05
3               Hotel  0.04
4                Café  0.04


----Condesa----
                  venue  freq
0    Mexican Restaurant  0.06
1            Restaurant  0.06
2  Gym / Fitness Center  0.04
3        Ice Cream Shop  0.04
4            Taco Place  0.03


----Cuauhtemoc----
                 venue  freq
0          Coffee Shop  0.09
1  Japanese Restaurant  0.08
2                 Café  0.06
3                Hotel  0.05
4   Mexican Restaurant  0.04


----Hipodromo----
                venue  freq
0  Mexican Restaurant  0.09
1          Taco Place  0.07
2          Restaurant  0.06
3         Coffee Shop  0.06
4                Café  0.04


----Hipodromo Condesa----
                venue  freq
0         Coffee Shop  0.07
1      Ice Cream Shop  0.06
2                 Spa  0.04
3                Café  0.03
4  Mexican Restaurant  0.03


----Juarez----
                venue  

## Obtain information about the characteristics of the business of interest to the client

In [16]:
latitude = best_1['Neighborhood Latitude'].values[1]
longitude = best_1['Neighborhood Longitude'].values[1]
search_query = 'Gourmet'
radius = 10000
LIMIT = 100
print(search_query + ' .... OK!')
url = 'https://api.foursquare.com/v2/venues/search?client_id={}&client_secret={}&ll={},{}&v={}&query={}&radius={}&limit={}'.format(CLIENT_ID, CLIENT_SECRET, latitude, longitude, VERSION, search_query, radius, LIMIT)
#url = 'https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(CLIENT_ID, CLIENT_SECRET,VERSION, latitude, longitude, radius, LIMIT)

latitude = best_1['Neighborhood Latitude'].values[1]
longitude = best_1['Neighborhood Longitude'].values[1]
search_query = 'Seafood'
radius = 10000
LIMIT = 100
print(search_query + ' .... OK!')
url_1 = 'https://api.foursquare.com/v2/venues/search?client_id={}&client_secret={}&ll={},{}&v={}&query={}&radius={}&limit={}'.format(CLIENT_ID, CLIENT_SECRET, latitude, longitude, VERSION, search_query, radius, LIMIT)

latitude = best_1['Neighborhood Latitude'].values[1]
longitude = best_1['Neighborhood Longitude'].values[1]
search_query = 'Meat'
radius = 10000
LIMIT = 100
print(search_query + ' .... OK!')
url_2 = 'https://api.foursquare.com/v2/venues/search?client_id={}&client_secret={}&ll={},{}&v={}&query={}&radius={}&limit={}'.format(CLIENT_ID, CLIENT_SECRET, latitude, longitude, VERSION, search_query, radius, LIMIT)

Gourmet .... OK!
Seafood .... OK!
Meat .... OK!


#### Get relevant part of JSON and transform it into a *pandas* dataframe

In [17]:
# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

In [18]:
results = requests.get(url).json()
results_1 = requests.get(url_1).json()
results_2 = requests.get(url_2).json()
# assign relevant part of JSON to venues
venues = results['response']['venues']
venues_1 = results_1['response']['venues']
venues_2 = results_2['response']['venues']
#venues = results['response']['groups'][0]['items']
dataframe = json_normalize(venues) # flatten JSON
dataframe_1 = json_normalize(venues_1)
dataframe_2 = json_normalize(venues_2)
# filter columns

# clean columns
dataframe.columns = [col.split(".")[-1] for col in dataframe.columns]
dataframe_1.columns = [col.split(".")[-1] for col in dataframe_1.columns]
dataframe_2.columns = [col.split(".")[-1] for col in dataframe_2.columns]

dataframe.head()

categories  hasPerk  \
0  [{'id': '4bf58dd8d48988d146941735', 'name': 'D...    False   
1  [{'id': '4bf58dd8d48988d1c4941735', 'name': 'R...    False   
2  [{'id': '4bf58dd8d48988d16d941735', 'name': 'C...    False   
3  [{'id': '4bf58dd8d48988d155941735', 'name': 'G...    False   
4  [{'id': '4bf58dd8d48988d1f6941735', 'name': 'D...    False   

                         id                    address  cc              city  \
0  4de006178877aab7fe3fe4c2                  Liverpool  MX  Ciudad de México   
1  5831052576f2ca684cb1f2a0               Parque Delta  MX  Ciudad de México   
2  4d17c95d1356a093bf5fde82            Ernesto Pugibet  MX  Ciudad de México   
3  51620227498efb317dafa81a  Av. Mariano Escobedo #435  MX  Ciudad de México   
4  4be718aabcef2d7feeda05e5      Av. 20 de Noviembre 3  MX  Ciudad de México   

  country                   crossStreet  distance  \
0  México                  Félix Cuevas      7942   
1  México                           NaN      3857   
2  México           Mercado de San Juan       828   
3  México                     Liverpool      4781   
4  México  Esq. con Venustiano Carranza       413   

                                    formattedAddress  \
0  [Liverpool (Félix Cuevas), 03100 Benito Juárez...   
1  [Parque Delta, Ciudad de México, Distrito Fede...   
2  [Ernesto Pugibet (Mercado de San Juan), Ciudad...   
3  [Av. Mariano Escobedo #435 (Liverpool), 11570 ...   
4  [Av. 20 de Noviembre 3 (Esq. con Venustiano Ca...   

                                      labeledLatLngs        lat        lng  \
0  [{'label': 'display', 'lat': 19.37326768881113...  19.373268 -99.178775   
1  [{'label': 'display', 'lat': 19.40276024708330...  19.402760 -99.155336   
2  [{'label': 'display', 'lat': 19.42993691481059...  19.429937 -99.144663   
3  [{'label': 'display', 'lat': 19.43449893034519...  19.434499 -99.183020   
4  [{'label': 'display', 'lat': 19.43111203883047...  19.431112 -99.134147   

  neighborhood postalCode             state                 name  \
0          NaN      03100  Distrito Federal  Experiencia Gourmet   
1          NaN        NaN  Distrito Federal  Experiencia Gourmet   
2          NaN        NaN  Distrito Federal  Triana Café Gourmet   
3          NaN      11570  Distrito Federal  Experiencia Gourmet   
4          NaN      06060  Distrito Federal    Palacio de Hierro   

     referralId   id  
0  v-1551036516  NaN  
1  v-1551036516  NaN  
2  v-1551036516  NaN  
3  v-1551036516  NaN  
4  v-1551036516  NaN

In [19]:
dataframe_1.head()

categories  hasPerk  \
0  [{'id': '4bf58dd8d48988d1ce941735', 'name': 'S...    False   
1  [{'id': '4bf58dd8d48988d1cc941735', 'name': 'S...    False   
2  [{'id': '4bf58dd8d48988d1ce941735', 'name': 'S...    False   
3  [{'id': '4bf58dd8d48988d1c4941735', 'name': 'R...    False   
4  [{'id': '4bf58dd8d48988d1ce941735', 'name': 'S...    False   

                         id          address  cc              city country  \
0  53a4a692498ef405d89c12fa       Clavelinas  MX  Ciudad de México  México   
1  5159da51e4b09bde5b97c4b5  Julio Verne 102  MX    Miguel Hidalgo  México   
2  544805f3498e175d6fca876e              NaN  MX               NaN  México   
3  507a4c80e4b0e94247cdd674              NaN  MX               NaN  México   
4  4bb12995f964a520a57f3ce3    Masaryk 360-4  MX  Ciudad de México  México   

        crossStreet  distance  \
0  Plan de San Luis      4659   
1          Virgilio      6186   
2               NaN      4657   
3               NaN      2798   
4    Pasaje Polanco      6228   

                                    formattedAddress  \
0  [Clavelinas (Plan de San Luis), 02800 Ciudad d...   
1  [Julio Verne 102 (Virgilio), 11560 mexico, Dis...   
2                                           [México]   
3                                           [México]   
4  [Masaryk 360-4 (Pasaje Polanco), 11560 Ciudad ...   

                                      labeledLatLngs        lat        lng  \
0  [{'label': 'display', 'lat': 19.46436978445854...  19.464370 -99.166957   
1  [{'label': 'display', 'lat': 19.43073878433507...  19.430739 -99.196380   
2  [{'label': 'display', 'lat': 19.46440375098107...  19.464404 -99.166889   
3  [{'label': 'display', 'lat': 19.42721754065844...  19.427218 -99.163424   
4  [{'label': 'display', 'lat': 19.43174767575296...  19.431748 -99.196813   

  postalCode             state                          name    referralId  \
0      02800  Distrito Federal     Sr.Camarón Seafood&Snacks  v-1551036517   
1      11560  Distrito Federal   PORTER Steakhouse & Seafood  v-1551036517   
2        NaN               NaN  Seafood & Sancks Sr. Camaron  v-1551036517   
3        NaN               NaN     El Nautico Fish & SeaFood  v-1551036517   
4      11560  Distrito Federal        Nautilus Seafood Grill  v-1551036517   

          id  
0  131291427  
1   76344354  
2        NaN  
3        NaN  
4   34997874

In [20]:
dataframe_2.head()

categories  hasPerk  \
0  [{'id': '4bf58dd8d48988d16c941735', 'name': 'B...    False   
1  [{'id': '4bf58dd8d48988d107941735', 'name': 'A...    False   
2  [{'id': '56aa371be4b08b9a8d573538', 'name': 'T...    False   
3  [{'id': '4bf58dd8d48988d11d951735', 'name': 'B...    False   
4  [{'id': '4bf58dd8d48988d1cb941735', 'name': 'F...    False   

                         id                    address  cc  \
0  536ff31c498ed481f50ec71e     Gandhi Esquina Reforma  MX   
1  51b2a19a498e2f0af0a0a167            Leibnitz No. 67  MX   
2  58ff3d6fc0af577da1b04808         Av Revolución 571a  MX   
3  516c2e3de4b0c8a40175eb95  Geranio #561 Col. La Raza  MX   
4  4ec1841d02d5a63a3fdd9e02                        NaN  MX   

                     city country         crossStreet  distance  \
0                     NaN  México                 NaN      4547   
1        Ciudad de México  México  Col. Nueva Anzurez      4268   
2  San Pedro de los Pinos  México            Calle 14      7138   
3            Azcapotzalco  México   Encarnacion Ortiz      3829   
4        Ciudad de México  México                 NaN      8926   

                                    formattedAddress  \
0                   [Gandhi Esquina Reforma, México]   
1  [Leibnitz No. 67 (Col. Nueva Anzurez), Ciudad ...   
2  [Av Revolución 571a (Calle 14), 03800 San Pedr...   
3  [Geranio #561 Col. La Raza (Encarnacion Ortiz)...   
4       [Ciudad de México, Distrito Federal, México]   

                                      labeledLatLngs        lat        lng  \
0  [{'label': 'display', 'lat': 19.42502760840725...  19.425028 -99.179969   
1  [{'label': 'display', 'lat': 19.428011, 'lng':...  19.428011 -99.177808   
2  [{'label': 'display', 'lat': 19.38834737052745...  19.388347 -99.186245   
3  [{'label': 'display', 'lat': 19.46559534448694...  19.465595 -99.149326   
4  [{'label': 'display', 'lat': 19.35749914182425...  19.357499 -99.109013   

  postalCode             state                        name    referralId  
0        NaN               NaN                   Meat Park  v-1551036517  
1        NaN  Distrito Federal                 Meats Prime  v-1551036517  
2      03800  Distrito Federal   La Comarca "Meat & Chips"  v-1551036517  
3      02990  Distrito Federal       Louisiana Meat México  v-1551036517  
4        NaN  Distrito Federal  Steak Meat Tacos al Carbón  v-1551036517

#### Define information of interest and filter dataframe

In [21]:
# keep only columns that include venue name, and anything that is associated with location
filtered_columns = ['name', 'categories'] + [col for col in dataframe.columns if col.startswith('location.')] + ['id'] +['lat']+['lng']
filtered_columns_1 = ['name', 'categories'] + [col for col in dataframe_1.columns if col.startswith('location.')] + ['id'] +['lat']+['lng']
filtered_columns_2 = ['name', 'categories'] + [col for col in dataframe_2.columns if col.startswith('location.')] + ['id'] +['lat']+['lng']
dataframe_filtered = dataframe.loc[:, filtered_columns]
dataframe_filtered_1 = dataframe_1.loc[:, filtered_columns_1]
dataframe_filtered_2 = dataframe_2.loc[:, filtered_columns_2]
# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

# filter the category for each row
dataframe_filtered['categories'] = dataframe_filtered.apply(get_category_type, axis=1)
dataframe_filtered_1['categories'] = dataframe_filtered_1.apply(get_category_type, axis=1)
dataframe_filtered_2['categories'] = dataframe_filtered_2.apply(get_category_type, axis=1)
# clean column names by keeping only last term
dataframe_filtered.columns = [column.split('.')[-1] for column in dataframe_filtered.columns]
dataframe_filtered_1.columns = [column.split('.')[-1] for column in dataframe_filtered_1.columns]
dataframe_filtered_2.columns = [column.split('.')[-1] for column in dataframe_filtered_2.columns]
dataframe_filtered

name              categories  \
0                        Experiencia Gourmet           Deli / Bodega   
1                        Experiencia Gourmet              Restaurant   
2                        Triana Café Gourmet                    Café   
3                        Experiencia Gourmet               Gastropub   
4                          Palacio de Hierro        Department Store   
5                  Debarbas Bebedero Gourmet                     Bar   
6                      Comida Gourmet Lupita              Restaurant   
7                        Experiencia Gourmet              Food Court   
8                              Pizza Gourmet             Pizza Place   
9                     La Esquina Del Gourmet              Taco Place   
10                      Café Gourmet Macondo                    Café   
11             Elefante Gourmet Delicatessen           Deli / Bodega   
12  Baguettes Gourmet & Charcutería Hinojosa           Deli / Bodega   
13                        U12 Bistro Gourmet                  Bistro   
14                 Debarbas Bebedero Gourmet         Other Nightlife   
15                      La Fonda del Gourmet              Restaurant   
16                              Bife Gourmet               BBQ Joint   
17                            Zotano Gourmet      Mexican Restaurant   
18                      tienda gourmet bequv           Deli / Bodega   
19                  fonda gourmet sin nombre      Mexican Restaurant   
20                                Le Gourmet       French Restaurant   
21           El Monasterio - Tamales Gourmet      Mexican Restaurant   
22                Burguerama Gourmet Texcoco            Burger Joint   
23            P.F. Rafa's gourmet restaurant                  Bistro   
24                              Mumu Gourmet                  Arcade   
25                           capital gourmet      Mexican Restaurant   
26                 Churros Chocolate Gourmet                Creperie   
27                     El Rinconcito Gourmet              Restaurant   
28                       De Pasadita Gourmet             Coffee Shop   
29                      Cafe Central Gourmet                    Café   
30                              Casa Gourmet             Pizza Place   
31                             Plaza Gourmet     Fried Chicken Joint   
32                     El Café, Cafe Gourmet                    Café   
33                           Bistrot Gourmet              Food Court   
34                             Sofìa gourmet             Salad Place   
35                      El Chilaquil Gourmet              Taco Place   
36                             Caffe Gourmet              Restaurant   
37                         La Lupita Gourmet  Furniture / Home Store   
38                             Pizza Gourmet             Pizza Place   
39                       Las Oaxacas Gourmet              Food Truck   
40                    Deli•Bajio 244 Gourmet             Coffee Shop   
41         Gourmet. Palacio De Hierro Centro          Chocolate Shop   
42                           Gourmet Palacio    Herbs & Spices Store   
43                             Salad Gourmet             Salad Place   
44          Al Punto y Coma Boutique Gourmet           Event Service   
45                             Rodea Gourmet          Farmers Market   
46                         Encuentro Gourmet             Coffee Shop   
47                Avith chocolateria gourmet             Coffee Shop   
48               burger gourmet keshet gaava            Burger Joint   
49                           Esquina Gourmet              Food Stand   

                          id         id        lat        lng  
0   4de006178877aab7fe3fe4c2        NaN  19.373268 -99.178775  
1   5831052576f2ca684cb1f2a0        NaN  19.402760 -99.155336  
2   4d17c95d1356a093bf5fde82        NaN  19.429937 -99.144663  
3   51620227498efb317dafa81a        NaN  19.434499 -99.183020  
4   4be718aabcef2d7feeda05e5        NaN  19.431

In [22]:
dataframe_filtered_1

name           categories  \
0              Sr.Camarón Seafood&Snacks   Seafood Restaurant   
1            PORTER Steakhouse & Seafood           Steakhouse   
2           Seafood & Sancks Sr. Camaron   Seafood Restaurant   
3              El Nautico Fish & SeaFood           Restaurant   
4                 Nautilus Seafood Grill   Seafood Restaurant   
5          Roma Beach Seafood Restaurant   Seafood Restaurant   
6                        Pacific Seafood                 None   
7                    sea food chef paris           Restaurant   
8    Sea food y comida tradicional Paris           Restaurant   
9                  House Seafood & Grill   Seafood Restaurant   
10                     Tremendos Seafood   Seafood Restaurant   
11                           Tony Roma's  American Restaurant   
12                       Mahalo Botanero                  Bar   
13           Mexican Seafood El Pacífico   Seafood Restaurant   
14            Barracuda Seafood & Drinks   Seafood Restaurant   
15                     Baby Fish Seafood   Seafood Restaurant   
16        Brol Pizza•Pasta•Seafood•Drink                  Pub   
17                   El Mejillon Seafood   Seafood Restaurant   
18  La Proa Excelencia en Frutos del Mar   Seafood Restaurant   
19               N.SANG TOMYAM & SEAFOOD      Thai Restaurant   
20                     Luna fish seafood   Seafood Restaurant   
21                       Makara Sea Food           Food Truck   
22                    Mariscos Baby Fish   Seafood Restaurant   
23         “El Barco” Seafood Of Colinas   Seafood Restaurant   
24                            Porfirio's   Mexican Restaurant   
25                Santa Patrona Sea Food   Seafood Restaurant   

                          id         id        lat        lng  
0   53a4a692498ef405d89c12fa  131291427  19.464370 -99.166957  
1   5159da51e4b09bde5b97c4b5   76344354  19.430739 -99.196380  
2   544805f3498e175d6fca876e        NaN  19.464404 -99.166889  
3   507a4c80e4b0e94247cdd674        NaN  19.427218 -99.163424  
4   4bb12995f964a520a57f3ce3   34997874  19.431748 -99.196813  
5   56e0975ccd10fb0882c2dfbb        NaN  19.412713 -99.083636  
6   4d7531e01a8aa35de0231aa7        NaN  19.433227 -99.174474  
7   5547ecf0498e12237c4cd9f5        NaN  19.428504 -99.159586  
8   560076d3498e786c586f35bb        NaN  19.428855 -99.159294  
9   4de95f071838b9ad8d26e86a        NaN  19.410332 -99.175919  
10  52d8cbee11d22d6544c24043        NaN  19.388927 -99.137406  
11  4b94284df964a520c26b34e3        NaN  19.431123 -99.183200  
12  579d43b6498ebfc7972d26a2        NaN  19.422631 -99.133434  
13  544aa8ff498ebace72196424        NaN  19.409895 -99.190156  
14  502eecafe4b060c1a52b4879        NaN  19.371342 -99.122276  
15  54b45420498e7aea128c166f        NaN  19.376871 -99.174165  
16  5914d55ce075500e9635d940        NaN  19.384845 -99.180915  
17  57098f44498e72d56be04080        NaN  19.393341 -99.211394  
18  548b4a0a498e66fce8800d49  114172454  19.464862 -99.180456  
19  4f0d948de4b05751687ae587        NaN  19.517510 -99.152525  
20  4d5d8ffb9895b1f76e81f10f        NaN  19.430012 -99.234190  
21  550f31f9498e1d661322a6ab        NaN  19.419213 -99.164932  
22  4df3efbeaeb7170aa2f2f756   50827828  19.376835 -99.193549  
23  5ba568661f8ed6002cba9875        NaN  19.367131 -99.229292  
24  5179c371e4b030a0e216dc70        NaN  19.349174 -99.189977  
25  519fdabc498e88b7f0c152ad        NaN  19.352008 -99.185852

In [23]:
dataframe_filtered_2

name                                categories  \
0                      Meat Park                              Burger Joint   
1                    Meats Prime                    Argentinian Restaurant   
2      La Comarca "Meat & Chips"                          Theme Restaurant   
3          Louisiana Meat México                                   Butcher   
4     Steak Meat Tacos al Carbón                                Food Truck   
5                   Meatless Bus                                Food Truck   
6        Food Truck Spartan meat                                Food Truck   
7               SM Sonora's Meat                                Restaurant   
8      US Meat Export Federation                                    Office   
9                       MeaToast                                Restaurant   
10                   Meat & Beer                                       Bar   
11                      MeaToast                            Sandwich Place   
12              Let's Meat Here!                                       Bar   
13               HUGLUTEO'S MEAT                                Steakhouse   
14                    meats club                                 Gastropub   
15                   The Meaties                        Mexican Restaurant   
16                   MEATVIANDE🐃                                    Winery   
17           Meatless Food Truck                                Food Truck   
18  Meats To Go (Carnes Premium)                                Steakhouse   
19                    Depa meats  Residential Building (Apartment / Condo)   
20                   Meats To Go                                    Market   
21                   Depa Meat's  Residential Building (Apartment / Condo)   
22                 Valtec' Meats                              Gourmet Shop   
23                    Depa Meats  Residential Building (Apartment / Condo)   
24                 VR Meats'Gays                                   Butcher   

                          id        lat        lng  
0   536ff31c498ed481f50ec71e  19.425028 -99.179969  
1   51b2a19a498e2f0af0a0a167  19.428011 -99.177808  
2   58ff3d6fc0af577da1b04808  19.388347 -99.186245  
3   516c2e3de4b0c8a40175eb95  19.465595 -99.149326  
4   4ec1841d02d5a63a3fdd9e02  19.357499 -99.109013  
5   526432e611d249468b145c68  19.424869 -99.156423  
6   56a18eb8498e8e3cfa0ab3cf  19.481441 -99.099094  
7   4bf1ba8b52bda59395e4b1b7  19.381534 -99.168455  
8   56c36aeccd10904e6d9286a7  19.437675 -99.209925  
9   573aa570498ef81110ccffd8  19.426542 -99.165339  
10  5aa2878879f6c70c313ef370  19.339916 -99.204260  
11  572ea292498e05a2d963fb1d  19.426958 -99.165247  
12  5b48d1ac6f706a002d40b652  19.357096 -99.122230  
13  52f61951498ee624b4bbf5d5  19.402227 -99.056679  
14  530d6601498e7e9988f0af6c  19.407158 -99.178320  
15  4e49822baeb7de71b38b77f4  19.496585 -99.160337  
16  5663cba238fa1e55a7de594b  19.415154 -99.064120  
17  5251d54411d25d7afb0a2366  19.440551 -99.224970  
18  50491395e4b076625c65b880  19.348922 -99.195283  
19  4f3dc446e4b01fd8583d716d  19.361240 -99.157247  
20  519ff4b8498ef989ed3badcb  19.349063 -99.195191  
21  56ff5111498e383cf77ad363  19.383403 -99.165318  
22  59398472c0f163445a41f577  19.357093 -99.113676  
23  4f3dc46fe4b0869411560c7d  19.363270 -99.156070  
24  4f2810e6e4b071524284f934  19.403879 -99.057490

## Obtain a map with the Business of interest 

In [24]:
address = 'Mexico City, MX'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude

# create map of Mexico using latitude and longitude values
map_mx = folium.Map(location=[latitude, longitude], zoom_start=11.48)

# add markers to map
for lat, lng, name, categories in zip(dataframe_filtered['lat'], dataframe_filtered['lng'], dataframe_filtered['name'], dataframe_filtered['categories']):
    label = '{}, {}'.format(name, categories)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_mx)  
    
# add markers to map
for lat, lng, name, categories in zip(dataframe_filtered_1['lat'], dataframe_filtered_1['lng'], dataframe_filtered_1['name'], dataframe_filtered_1['categories']):
    label = '{}, {}'.format(name, categories)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='violet',
        fill=True,
        fill_color='#5186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_mx)      

    # add markers to map
for lat, lng, name, categories in zip(dataframe_filtered_2['lat'], dataframe_filtered_2['lng'], dataframe_filtered_2['name'], dataframe_filtered_2['categories']):
    label = '{}, {}'.format(name, categories)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='red',
        fill=True,
        fill_color='#8186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_mx)   
    
map_mx
    

### make a dataframe from the resutls 

In [25]:

df_1=dataframe_filtered.drop(['id'], axis=1)
df_2=dataframe_filtered_1.drop(['id'], axis=1)
df_3=dataframe_filtered_2.drop(['id'], axis=1)
df1 = df_1.append(df_2,ignore_index=True)
data = df1.append(df_3,ignore_index=True)
data

name  \
0                         Experiencia Gourmet   
1                         Experiencia Gourmet   
2                         Triana Café Gourmet   
3                         Experiencia Gourmet   
4                           Palacio de Hierro   
5                   Debarbas Bebedero Gourmet   
6                       Comida Gourmet Lupita   
7                         Experiencia Gourmet   
8                               Pizza Gourmet   
9                      La Esquina Del Gourmet   
10                       Café Gourmet Macondo   
11              Elefante Gourmet Delicatessen   
12   Baguettes Gourmet & Charcutería Hinojosa   
13                         U12 Bistro Gourmet   
14                  Debarbas Bebedero Gourmet   
15                       La Fonda del Gourmet   
16                               Bife Gourmet   
17                             Zotano Gourmet   
18                       tienda gourmet bequv   
19                   fonda gourmet sin nombre   
20                                 Le Gourmet   
21            El Monasterio - Tamales Gourmet   
22                 Burguerama Gourmet Texcoco   
23             P.F. Rafa's gourmet restaurant   
24                               Mumu Gourmet   
25                            capital gourmet   
26                  Churros Chocolate Gourmet   
27                      El Rinconcito Gourmet   
28                        De Pasadita Gourmet   
29                       Cafe Central Gourmet   
30                               Casa Gourmet   
31                              Plaza Gourmet   
32                      El Café, Cafe Gourmet   
33                            Bistrot Gourmet   
34                              Sofìa gourmet   
35                       El Chilaquil Gourmet   
36                              Caffe Gourmet   
37                          La Lupita Gourmet   
38                              Pizza Gourmet   
39                        Las Oaxacas Gourmet   
40                     Deli•Bajio 244 Gourmet   
41          Gourmet. Palacio De Hierro Centro   
42                            Gourmet Palacio   
43                              Salad Gourmet   
44           Al Punto y Coma Boutique Gourmet   
45                              Rodea Gourmet   
46                          Encuentro Gourmet   
47                 Avith chocolateria gourmet   
48                burger gourmet keshet gaava   
49                            Esquina Gourmet   
50                  Sr.Camarón Seafood&Snacks   
51                PORTER Steakhouse & Seafood   
52               Seafood & Sancks Sr. Camaron   
53                  El Nautico Fish & SeaFood   
54                     Nautilus Seafood Grill   
55              Roma Beach Seafood Restaurant   
56                            Pacific Seafood   
57                        sea food chef paris   
58        Sea food y comida tradicional Paris   
59                      House Seafood & Grill   
60                          Tremendos Seafood   
61                                Tony Roma's   
62                            Mahalo Botanero   
63                Mexican Seafood El Pacífico   
64                 Barracuda Seafood & Drinks   
65                          Baby Fish Seafood   
66             Brol Pizza•Pasta•Seafood•Drink   
67                        El Mejillon Seafood   
68       La Proa Excelencia en Frutos del Mar   
69                    N.SANG TOMYAM & SEAFOOD   
70                          Luna fish seafood   
71                            Makara Sea Food   
72                         Mariscos Baby Fish   
73              “El Barco” Seafood Of Colinas   
74                                 Porfirio's   
75                     Santa Patrona Sea Food   
76                                  Meat Park   
77                                Meats Prime   
78                  La Comarca "Meat & Chips"   
79                      Louisiana Meat México   
80                 Steak Meat Tacos al Carbón   
81                     

## Create the new dataframe and display the top 10 venues for the principal neighborhoods .

In [26]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]


num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = mx_grouped['Neighborhood']

for ind in np.arange(mx_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(mx_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()




Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0             Centro    Mexican Restaurant                   Bar   
1            Condesa            Restaurant    Mexican Restaurant   
2         Cuauhtemoc           Coffee Shop   Japanese Restaurant   
3          Hipodromo    Mexican Restaurant            Taco Place   
4  Hipodromo Condesa           Coffee Shop        Ice Cream Shop   

  3rd Most Common Venue 4th Most Common Venue          5th Most Common Venue  \
0                Bakery                 Hotel                           Café   
1        Ice Cream Shop  Gym / Fitness Center  Vegetarian / Vegan Restaurant   
2                  Café                 Hotel                 Ice Cream Shop   
3            Restaurant           Coffee Shop                           Café   
4                   Spa           Pizza Place                           Café   

  6th Most Common Venue   7th Most Common Venue 8th Most Common Venue  \
0        Ice Cream Shop             Coffee Shop            Art Museum   
1           Coffee Shop              Taco Place                Bakery   
2     French Restaurant              Taco Place    Italian Restaurant   
3    Seafood Restaurant  Argentinian Restaurant        Ice Cream Shop   
4                Bistro            Burger Joint            Restaurant   

  9th Most Common Venue 10th Most Common Venue  
0           Art Gallery               Boutique  
1                   Bar     Italian Restaurant  
2    Mexican Restaurant     Seafood Restaurant  
3                   Bar               Tea Room  
4    Mexican Restaurant             Taco Place

## Clustering

The process will consist in obtaining first the venues with the characteristics that we are looking for in your category.

once obtained these data, they will be contrasted with the most visited places in these Boroughs.

To carry out this analysis, a cluster will be made regarding the most visited venues in the Boroughs Miguel Hidalgo and Cuautemoc.

In this step we will compare how the most visited places are geographically related to the target venues in our project.

Once we have said analysis, we will obtain the information of the venues of interest and the most visited ones but for the Borough Benito Juarez, which is the Borough where the client wishes to open his new business.

# Cluster Neighborhoods

Run *k*-means to cluster the neighborhood into 5 clusters.

In [27]:
# set number of clusters
kclusters = 5

mx_grouped_clustering = mx_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(mx_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([3, 1, 2, 1, 0, 4, 4], dtype=int32)

In [28]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

t_merged = best_1

t_merged = t_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

t_merged.head() # check the last columns!

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
154       Centro              19.433056                -99.1375   
155       Centro              19.433056                -99.1375   
156       Centro              19.433056                -99.1375   
157       Centro              19.433056                -99.1375   
158       Centro              19.433056                -99.1375   

                                                 Venue  Venue Latitude  \
154                            Hotel Historico Central       19.433153   
155  Palacio de Cultura Banamex - Antiguo Palacio d...       19.433681   
156                                     Casino Español       19.433023   
157                                    Downtown México       19.432875   
158                                     Azul Histórico       19.432880   

     Venue Longitude      Venue Category  Cluster Labels  \
154       -99.138376               Hotel               3   
155       -99.139018          Art Museum               3   
156       -99.137110  Spanish Restaurant               3   
157       -99.136208               Hotel               3   
158       -99.136197  Mexican Restaurant               3   

    1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
154    Mexican Restaurant                   Bar                Bakery   
155    Mexican Restaurant                   Bar                Bakery   
156    Mexican Restaurant                   Bar                Bakery   
157    Mexican Restaurant                   Bar                Bakery   
158    Mexican Restaurant                   Bar                Bakery   

    4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
154                 Hotel                  Café        Ice Cream Shop   
155                 Hotel                  Café        Ice Cream Shop   
156                 Hotel                  Café        Ice Cream Shop   
157                 Hotel                  Café        Ice Cream Shop   
158                 Hotel                  Café        Ice Cream Shop   

    7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
154           Coffee Shop            Art Museum           Art Gallery   
155           Coffee Shop            Art Museum           Art Gallery   
156           Coffee Shop            Art Museum           Art Gallery   
157           Coffee Shop            Art Museum           Art Gallery   
158           Coffee Shop            Art Museum           Art Gallery   

    10th Most Common Venue  
154               Boutique  
155               Boutique  
156               Boutique  
157               Boutique  
158               Boutique

## Obtain a map with the cluster of top venues in the Boroughs of interest and the target bussines

In [29]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(t_merged['Neighborhood Latitude'], t_merged['Neighborhood Longitude'], t_merged['Neighborhood'], t_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=25,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.9).add_to(map_clusters)
# add markers to map
for lat, lng, name, categories in zip(dataframe_filtered['lat'], dataframe_filtered['lng'], dataframe_filtered['name'], dataframe_filtered['categories']):
    label = '{}, {}'.format(name, categories)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_clusters)  
    
# add markers to map
for lat, lng, name, categories in zip(dataframe_filtered_1['lat'], dataframe_filtered_1['lng'], dataframe_filtered_1['name'], dataframe_filtered_1['categories']):
    label = '{}, {}'.format(name, categories)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='violet',
        fill=True,
        fill_color='#5186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_clusters)      

    # add markers to map
for lat, lng, name, categories in zip(dataframe_filtered_2['lat'], dataframe_filtered_2['lng'], dataframe_filtered_2['name'], dataframe_filtered_2['categories']):
    label = '{}, {}'.format(name, categories)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='red',
        fill=True,
        fill_color='#8186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_clusters)     
       
map_clusters

## Target Borough

Within the Borough target that is Benito Juárez, it was found which is the neighborhood with the greatest potential due to its proximity to the top venues previously analyzed. Once the target neighborhood has been selected, the venues of that neighborhood are obtained and filtered with respect to which already exist that its category is similar to that which the client seeks to open.

In this case, you get what category of venue is needed in that neighborhood and what is the distribution of the other venues for that geographical area

### Get the data of the Borough where our client prospects his business

In [30]:
df_ben= df.loc[(df['Borough'] == 'Benito Juarez')]
print(df_ben.count())

Borough         53
Neighborhood    53
Latitude        53
Longitude       53
dtype: int64


In [31]:
mx_venues_b = getNearbyVenues(names=df_ben['Neighborhood'],
                                   latitudes=df_ben['Latitude'],
                                   longitudes=df_ben['Longitude']
                                  )

mx_venues_b.head()

8 de Agosto
Acacias
Actipan
Alamos
Albert
Americas Unidas
Ampliacion Napoles
Atenor Salas
Ciudad de los Deportes
Colonia del Carmen
Colonia del Lago
Colonia del Valle Centro
Colonia del Valle Norte
Colonia del Valle Sur
Credito Constructor
Ermita
Extremadura Insurgentes
General Pedro Maria Anaya
Independencia
Insurgentes Mixcoac
Insurgentes San Borja
Iztaccihuatl
Josefa Ortiz de Dominguez
Letran Valle
Merced Gomez
Miguel Aleman
Miravalle
Mixcoac
Moderna
Napoles
Narvarte Oriente
Narvarte Poniente
Nativitas
Niños Heroes
Noche Buena
Periodista
Piedad Narvarte
Portales Norte
Portales Oriente
Portales Sur
Postal
Residencial Emperadores
San Jose Insurgentes
San Juan
San Pedro de los Pinos
San Simon Ticumac
Santa Cruz Atoyac
Santa Maria Nonoalco
Tlacoquemecatl
Vertiz Narvarte
Villa de Cortes
Xoco
Zacahuitzco


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0  8 de Agosto              19.394167              -99.186944   
1  8 de Agosto              19.394167              -99.186944   
2  8 de Agosto              19.394167              -99.186944   
3  8 de Agosto              19.394167              -99.186944   
4  8 de Agosto              19.394167              -99.186944   

                              Venue  Venue Latitude  Venue Longitude  \
0                        Tacos Chuy       19.395276       -99.186512   
1                      Barniacs GYM       19.394320       -99.185260   
2             Librería del Ermitaño       19.392323       -99.186814   
3  Courtyard Mexico City Revolucion       19.396538       -99.185579   
4                        Skrap Pack       19.394564       -99.185169   

      Venue Category  
0         Food Truck  
1                Gym  
2        Coffee Shop  
3              Hotel  
4  Martial Arts Dojo

# Results 

### Let's check the venues in this Borough

In [32]:
df_filt_2=pd.DataFrame(mx_venues_b.groupby('Neighborhood').count())
best_N2 = df_filt_2.loc[df_filt_2['Venue'].values==100].index.values
ben=mx_venues_b.loc[mx_venues_b['Neighborhood'].isin(best_N2)]
ben.head()

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
76      Actipan              19.368333              -99.178611   
77      Actipan              19.368333              -99.178611   
78      Actipan              19.368333              -99.178611   
79      Actipan              19.368333              -99.178611   
80      Actipan              19.368333              -99.178611   

                 Venue  Venue Latitude  Venue Longitude  \
76  Sonora Grill Prime       19.368419       -99.180659   
77        Latente Café       19.367725       -99.177624   
78        Sports World       19.368758       -99.180809   
79   La Vaca Argentina       19.368792       -99.181146   
80     Academia Bartec       19.370023       -99.178688   

            Venue Category  
76              Steakhouse  
77                    Café  
78    Gym / Fitness Center  
79  Argentinian Restaurant  
80            Dance Studio

##  Analyze the Borough

In [33]:
# one hot encoding
b_onehot = pd.get_dummies(ben[['Venue Category']], prefix="", prefix_sep="")
# add neighborhood column back to dataframe
b_onehot['Neighborhood'] = ben['Neighborhood'] 
# move neighborhood column to the first column
b_onehot = b_onehot.set_index('Neighborhood').reset_index()
# create the fixed columns
fixed_columns = [b_onehot.columns[0]] + b_onehot.columns[1:].values.tolist() 
b_onehot = b_onehot[fixed_columns]
b_onehot.head()

Neighborhood  American Restaurant  Argentinian Restaurant  Art Gallery  \
0      Actipan                    0                       0            0   
1      Actipan                    0                       0            0   
2      Actipan                    0                       0            0   
3      Actipan                    0                       1            0   
4      Actipan                    0                       0            0   

   Art Museum  Arts & Entertainment  Asian Restaurant  Auto Garage  \
0           0                     0                 0            0   
1           0                     0                 0            0   
2           0                     0                 0            0   
3           0                     0                 0            0   
4           0                     0                 0            0   

   Auto Workshop  Automotive Shop  BBQ Joint  Baby Store  Bagel Shop  Bakery  \
0              0                0          0           0           0       0   
1              0                0          0           0           0       0   
2              0                0          0           0           0       0   
3              0                0          0           0           0       0   
4              0                0          0           0           0       0   

   Bar  Bed & Breakfast  Beer Bar  Beer Store  Bike Rental / Bike Share  \
0    0                0         0           0                         0   
1    0                0         0           0                         0   
2    0                0         0           0                         0   
3    0                0         0           0                         0   
4    0                0         0           0                         0   

   Bistro  Bookstore  Boutique  Bowling Green  Brazilian Restaurant  \
0       0          0         0              0                     0   
1       0          0         0              0                     0   
2       0          0         0              0                     0   
3       0          0         0              0                     0   
4       0          0         0              0                     0   

   Breakfast Spot  Brewery  Bridal Shop  Building  Burger Joint  \
0               0        0            0         0             0   
1               0        0            0         0             0   
2               0        0            0         0             0   
3               0        0            0         0             0   
4               0        0            0         0             0   

   Burrito Place  Cafeteria  Café  Candy Store  Casino  Cheese Shop  \
0              0          0     0            0       0            0   
1              0          0     1            0       0            0   
2              0          0     0            0       0            0   
3              0          0     0            0       0            0   
4              0          0     0            0       0            0   

   Chinese Restaurant  Clothing Store  Cocktail Bar  Coffee Shop  \
0                   0               0             0            0   
1                   0               0             0            0   
2                   0               0             0            0   
3                   0               0             0            0   
4                   0               0             0            0   

   Comfort Food Restaurant  Comic Shop  Concert Hall  Convenience Store  \
0                        0           0             0                  0   
1                        0           0             0                  0   
2                        0           0             0                  0   
3                        0           0             0                  0   
4                        0           0             0                  0   

   Cosmetics Shop  Creperie  Cultural Center  Cupcake Shop  Dance Studio  \

#### Next, let's group rows by neighborhood and by taking the mean of the frequency of occurrence of each category

In [34]:
b_grouped = b_onehot.groupby('Neighborhood').mean().reset_index()
b_grouped

Neighborhood  American Restaurant  Argentinian Restaurant  \
0                 Actipan                 0.00                    0.03   
1      Ampliacion Napoles                 0.02                    0.03   
2  Ciudad de los Deportes                 0.01                    0.03   
3     Insurgentes Mixcoac                 0.00                    0.03   
4                 Napoles                 0.00                    0.01   
5         Piedad Narvarte                 0.01                    0.00   
6                    Xoco                 0.02                    0.00   

   Art Gallery  Art Museum  Arts & Entertainment  Asian Restaurant  \
0         0.00        0.00                  0.00              0.00   
1         0.01        0.00                  0.00              0.00   
2         0.00        0.00                  0.00              0.00   
3         0.01        0.00                  0.01              0.00   
4         0.01        0.01                  0.00              0.01   
5         0.00        0.00                  0.00              0.00   
6         0.01        0.00                  0.00              0.00   

   Auto Garage  Auto Workshop  Automotive Shop  BBQ Joint  Baby Store  \
0         0.00           0.00             0.00       0.00        0.00   
1         0.01           0.01             0.00       0.01        0.00   
2         0.00           0.00             0.00       0.02        0.00   
3         0.00           0.00             0.01       0.00        0.01   
4         0.00           0.00             0.00       0.01        0.00   
5         0.00           0.00             0.00       0.00        0.00   
6         0.00           0.00             0.00       0.00        0.00   

   Bagel Shop  Bakery   Bar  Bed & Breakfast  Beer Bar  Beer Store  \
0        0.01    0.04  0.00             0.00      0.01        0.01   
1        0.00    0.03  0.01             0.01      0.00        0.00   
2        0.00    0.05  0.00             0.00      0.00        0.00   
3        0.01    0.02  0.01             0.00      0.01        0.00   
4        0.00    0.01  0.01             0.01      0.00        0.00   
5        0.00    0.00  0.01             0.00      0.00        0.00   
6        0.00    0.01  0.00             0.00      0.00        0.00   

   Bike Rental / Bike Share  Bistro  Bookstore  Boutique  Bowling Green  \
0                      0.00    0.01       0.00      0.00           0.01   
1                      0.00    0.02       0.00      0.00           0.00   
2                      0.00    0.00       0.00      0.00           0.00   
3                      0.00    0.00       0.00      0.00           0.01   
4                      0.01    0.00       0.00      0.01           0.00   
5                      0.01    0.00       0.01      0.04           0.00   
6                      0.00    0.00       0.02      0.04           0.00   

   Brazilian Restaurant  Breakfast Spot  Brewery  Bridal Shop  Building  \
0                  0.00            0.00     0.01         0.00      0.00   
1                  0.00            0.03     0.00         0.00      0.00   
2                  0.00            0.02     0.00         0.00      0.00   
3                  0.00            0.01     0.00         0.00      0.01   
4                  0.01            0.02     0.00         0.01      0.00   
5                  0.00            0.01     0.01         0.00      0.00   
6                  0.00            0.01     0.00         0.00      0.00   

   Burger Joint  Burrito Place  Cafeteria  Café  Candy Store  Casino  \
0          0.02           0.00       0.01  0.03         0.00    0.00   
1          0.01           0.00       0.00  0.05         0.00    0.01   
2          0.01           0.00       0.00  0.02         0.00    0.00   
3          0.00           0.00       0.00  0.01         0.00    0.00   
4          0.03           0.00       0.00  0.04         0.00    0.00   
5          0.04           0.01       0.01  0.01         0.00    0.00   
6      

#### Let's print each neighborhood along with the top 10 most common venues

In [35]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]


num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
b_venues_sorted = pd.DataFrame(columns=columns)
b_venues_sorted['Neighborhood'] = b_grouped['Neighborhood']

for ind in np.arange(b_grouped.shape[0]):
    b_venues_sorted.iloc[ind, 1:] = return_most_common_venues(b_grouped.iloc[ind, :], num_top_venues)

b_venues_sorted.head()

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0                 Actipan           Coffee Shop        Cosmetics Shop   
1      Ampliacion Napoles        Ice Cream Shop            Restaurant   
2  Ciudad de los Deportes    Mexican Restaurant            Taco Place   
3     Insurgentes Mixcoac           Coffee Shop    Mexican Restaurant   
4                 Napoles           Coffee Shop    Mexican Restaurant   

  3rd Most Common Venue 4th Most Common Venue   5th Most Common Venue  \
0            Restaurant                Bakery  Argentinian Restaurant   
1                  Café    Mexican Restaurant             Coffee Shop   
2            Restaurant    Seafood Restaurant                  Bakery   
3           Pizza Place        Cosmetics Shop                   Diner   
4                  Café    Italian Restaurant                     Spa   

    6th Most Common Venue   7th Most Common Venue 8th Most Common Venue  \
0              Taco Place                    Café    Mexican Restaurant   
1      Seafood Restaurant             Pizza Place                Bakery   
2  Argentinian Restaurant                    Café     Convenience Store   
3              Taco Place  Argentinian Restaurant            Restaurant   
4            Burger Joint             Pizza Place        Ice Cream Shop   

  9th Most Common Venue 10th Most Common Venue  
0      Toy / Game Store             Steakhouse  
1        Breakfast Spot     Italian Restaurant  
2          Dessert Shop             Steakhouse  
3   Sporting Goods Shop   Gym / Fitness Center  
4   Japanese Restaurant             Taco Place

# Cluster Neighborhoods

In [36]:
# set number of clusters
k1clusters = 5

b_grouped_clustering = b_grouped.drop('Neighborhood', 1)

# run k-means clustering
b_kmeans = KMeans(n_clusters=k1clusters, random_state=0).fit(b_grouped_clustering)

# check cluster labels generated for each row in the dataframe
b_kmeans.labels_[0:10] 

array([1, 3, 2, 1, 0, 4, 4], dtype=int32)

### Let's create a new dataframe that includes the cluster as well as the top 10 venues for each neighborhood.

In [37]:
# add clustering labels
b_venues_sorted.insert(0, 'Cluster Labels', b_kmeans.labels_)

b_merged = ben

b_merged = b_merged.join(b_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

b_merged.head() # check the last columns!

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
76      Actipan              19.368333              -99.178611   
77      Actipan              19.368333              -99.178611   
78      Actipan              19.368333              -99.178611   
79      Actipan              19.368333              -99.178611   
80      Actipan              19.368333              -99.178611   

                 Venue  Venue Latitude  Venue Longitude  \
76  Sonora Grill Prime       19.368419       -99.180659   
77        Latente Café       19.367725       -99.177624   
78        Sports World       19.368758       -99.180809   
79   La Vaca Argentina       19.368792       -99.181146   
80     Academia Bartec       19.370023       -99.178688   

            Venue Category  Cluster Labels 1st Most Common Venue  \
76              Steakhouse               1           Coffee Shop   
77                    Café               1           Coffee Shop   
78    Gym / Fitness Center               1           Coffee Shop   
79  Argentinian Restaurant               1           Coffee Shop   
80            Dance Studio               1           Coffee Shop   

   2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
76        Cosmetics Shop            Restaurant                Bakery   
77        Cosmetics Shop            Restaurant                Bakery   
78        Cosmetics Shop            Restaurant                Bakery   
79        Cosmetics Shop            Restaurant                Bakery   
80        Cosmetics Shop            Restaurant                Bakery   

     5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
76  Argentinian Restaurant            Taco Place                  Café   
77  Argentinian Restaurant            Taco Place                  Café   
78  Argentinian Restaurant            Taco Place                  Café   
79  Argentinian Restaurant            Taco Place                  Café   
80  Argentinian Restaurant            Taco Place                  Café   

   8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
76    Mexican Restaurant      Toy / Game Store             Steakhouse  
77    Mexican Restaurant      Toy / Game Store             Steakhouse  
78    Mexican Restaurant      Toy / Game Store             Steakhouse  
79    Mexican Restaurant      Toy / Game Store             Steakhouse  
80    Mexican Restaurant      Toy / Game Store             Steakhouse

## Visualize the resulting clusters

In [38]:
# create map
map_b = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(b_merged['Neighborhood Latitude'], b_merged['Neighborhood Longitude'], b_merged['Neighborhood'], b_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=25,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_b)
       
map_b

### Add to the map the target businnes to analyze

In [52]:

# create map
map_b = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(b_merged['Neighborhood Latitude'], b_merged['Neighborhood Longitude'], b_merged['Neighborhood'], b_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=25,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_b)
       
map_b


# add markers to map
for lat, lng, name, categories in zip(dataframe_filtered['lat'], dataframe_filtered['lng'], dataframe_filtered['name'], dataframe_filtered['categories']):
    label = '{}, {}'.format(name, categories)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_b)  
    
# add markers to map
for lat, lng, name, categories in zip(dataframe_filtered_1['lat'], dataframe_filtered_1['lng'], dataframe_filtered_1['name'], dataframe_filtered_1['categories']):
    label = '{}, {}'.format(name, categories)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='violet',
        fill=True,
        fill_color='#5186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_b)      

    # add markers to map
for lat, lng, name, categories in zip(dataframe_filtered_2['lat'], dataframe_filtered_2['lng'], dataframe_filtered_2['name'], dataframe_filtered_2['categories']):
    label = '{}, {}'.format(name, categories)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='red',
        fill=True,
        fill_color='#8186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_b)  
map_b    

### View the map and the cluster with most visit venues, for Neighborhood of opotunity in the target Borough take a look in Narvarte Poniente Neighborhood

In [53]:
df_narv= df.loc[(df['Neighborhood'] == 'Narvarte Poniente')]
df_narv

Borough       Neighborhood   Latitude  Longitude
789  Benito Juarez  Narvarte Poniente  19.390278 -99.158056

### Let's check the venues in this Neighborhood

In [59]:
nav_ven=mx_venues_b.loc[mx_venues_b['Neighborhood']=='Narvarte Poniente']
nav_ven

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
2071  Narvarte Poniente              19.390278              -99.158056   
2072  Narvarte Poniente              19.390278              -99.158056   
2073  Narvarte Poniente              19.390278              -99.158056   
2074  Narvarte Poniente              19.390278              -99.158056   
2075  Narvarte Poniente              19.390278              -99.158056   
2076  Narvarte Poniente              19.390278              -99.158056   
2077  Narvarte Poniente              19.390278              -99.158056   
2078  Narvarte Poniente              19.390278              -99.158056   
2079  Narvarte Poniente              19.390278              -99.158056   
2080  Narvarte Poniente              19.390278              -99.158056   
2081  Narvarte Poniente              19.390278              -99.158056   
2082  Narvarte Poniente              19.390278              -99.158056   
2083  Narvarte Poniente              19.390278              -99.158056   
2084  Narvarte Poniente              19.390278              -99.158056   
2085  Narvarte Poniente              19.390278              -99.158056   
2086  Narvarte Poniente              19.390278              -99.158056   
2087  Narvarte Poniente              19.390278              -99.158056   
2088  Narvarte Poniente              19.390278              -99.158056   
2089  Narvarte Poniente              19.390278              -99.158056   
2090  Narvarte Poniente              19.390278              -99.158056   
2091  Narvarte Poniente              19.390278              -99.158056   
2092  Narvarte Poniente              19.390278              -99.158056   
2093  Narvarte Poniente              19.390278              -99.158056   
2094  Narvarte Poniente              19.390278              -99.158056   
2095  Narvarte Poniente              19.390278              -99.158056   
2096  Narvarte Poniente              19.390278              -99.158056   
2097  Narvarte Poniente              19.390278              -99.158056   
2098  Narvarte Poniente              19.390278              -99.158056   
2099  Narvarte Poniente              19.390278              -99.158056   
2100  Narvarte Poniente              19.390278              -99.158056   
2101  Narvarte Poniente              19.390278              -99.158056   
2102  Narvarte Poniente              19.390278              -99.158056   
2103  Narvarte Poniente              19.390278              -99.158056   
2104  Narvarte Poniente              19.390278              -99.158056   
2105  Narvarte Poniente              19.390278              -99.158056   
2106  Narvarte Poniente              19.390278              -99.158056   
2107  Narvarte Poniente              19.390278              -99.158056   
2108  Narvarte Poniente              19.390278              -99.158056   
2109  Narvarte Poniente              19.390278              -99.158056   
2110  Narvarte Poniente              19.390278              -99.158056   
2111  Narvarte Poniente              19.390278              -99.158056   
2112  Narvarte Poniente              19.390278              -99.158056   
2113  Narvarte Poniente              19.390278              -99.158056   
2114  Narvarte Poniente              19.390278              -99.158056   
2115  Narvarte Poniente              19.390278              -99.158056   
2116  Narvarte Poniente              19.390278              -99.158056   
2117  Narvarte Poniente              19.390278              -99.158056   
2118  Narvarte Poniente              19.390278              -99.158056   
2119  Narvarte Poniente              19.390278              -99.158056   
2120  Narvarte Poniente              19.390278              -99.158056   
2121  Narvarte Poniente              19.390278              -99.158056   
2122  Narvarte Poniente              19.390278              -99.158056   
2123  Narvarte Poniente              19.390278              -99.158056   
2124  Narvarte 

### Which of these businesses belong to the same category that our client intends to open

In [74]:
f1=nav_ven.loc[nav_ven['Venue Category'].str.contains('Steakhouse')]
f2=nav_ven.loc[nav_ven['Venue Category'].str.contains('Gourmet')]
f3=nav_ven.loc[nav_ven['Venue Category'].str.contains('Seafood')]
f4=nav_ven.loc[nav_ven['Venue Category'].str.contains('Meat')]

f1 = f1.append(f2,ignore_index=True)
data = f1.append(f3,ignore_index=True)
data_f = data.append(f4,ignore_index=True)
data_f

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0  Narvarte Poniente              19.390278              -99.158056   
1  Narvarte Poniente              19.390278              -99.158056   

          Venue  Venue Latitude  Venue Longitude      Venue Category  
0  Sonora Grill       19.393172       -99.160590          Steakhouse  
1     Punta Mar       19.391012       -99.158261  Seafood Restaurant

### Add to the map the businnes in the new target Neighborhood 

In [82]:
latitude = nav_ven['Neighborhood Latitude'].iloc[0]
longitude = nav_ven['Neighborhood Longitude'].iloc[0]
# create map
map_b = folium.Map(location=[latitude, longitude], zoom_start=15)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(b_merged['Neighborhood Latitude'], b_merged['Neighborhood Longitude'], b_merged['Neighborhood'], b_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=25,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_b)
       
map_b


# add markers to map
for lat, lng, name, categories in zip(dataframe_filtered['lat'], dataframe_filtered['lng'], dataframe_filtered['name'], dataframe_filtered['categories']):
    label = '{}, {}'.format(name, categories)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_b)  
    
# add markers to map
for lat, lng, name, categories in zip(dataframe_filtered_1['lat'], dataframe_filtered_1['lng'], dataframe_filtered_1['name'], dataframe_filtered_1['categories']):
    label = '{}, {}'.format(name, categories)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='violet',
        fill=True,
        fill_color='#5186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_b)      

    # add markers to map
for lat, lng, name, categories in zip(dataframe_filtered_2['lat'], dataframe_filtered_2['lng'], dataframe_filtered_2['name'], dataframe_filtered_2['categories']):
    label = '{}, {}'.format(name, categories)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='red',
        fill=True,
        fill_color='#8186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_b)  
    
    # add markers to map
for lat, lng, name, categories in zip(nav_ven['Venue Latitude'], nav_ven['Venue Longitude'], nav_ven['Venue'], nav_ven['Venue Category']):
    label = '{}, {}'.format(name, categories)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='cyan',
        fill=True,
        fill_color='gray',
        fill_opacity=0.7,
        parse_html=False).add_to(map_b)      
    
    
for lat, lng, name, categories in zip(data_f['Venue Latitude'], data_f['Venue Longitude'], data_f['Venue'], data_f['Venue Category']):
    label = '{}, {}'.format(name, categories)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='red',
        fill=True,
        fill_color='red',
        fill_opacity=0.7,
        parse_html=False).add_to(map_b)          
    
    
map_b    

In this analysis we were able to observe which are the largest venues in the city of Mexico that belong to the Cuautemoc Boroughs and Miguel Hidalgo, as well as where the areas of greatest concentration of people that can be potential clients are located.

The areas with the highest concentration of successful venues showed us a behavior with respect to the venues of the target category to which we want to describe.

It is common for these to be near the most visited venues or venues top, however there is some relaxation in distance with respect to these clusters.

The economic sector of the people who visit the venues of the two main Boroughs of this study is greater than what is intended to be opened in the Benito Juarez Borough.

The Narvarte Poniente neighborhood represents a potential area for a place specializing in aged meat and gourmet products, due to the closeness it has with well-visited venues and the fact that there is no such business in the neighborhood.

# Discussion 

### Access to Foursquare
One of the issues to improve the study is to have greater access to queries in Foursquare to have a larger database and to make predictions with more formidable data.

The large number of neighborhoods that Mexico City contains makes it more convenient to do this analysis with queries on Foursquare that require premium queries.

### Venues categories

Specialized gourmet places in Mexico City sometimes do not carry a good categorization in the field of venue category that offers foursquare.
It is useful in future studies access to data that are not specifically of this tool to give more support to the real category that the venues have.

# Conclusion 

From the study we can conclude that the Benito Juarez Borough is a potential location for the establishment of gourmet venues due to the good geographic location that exists with the most frequented venues of the clientele that prefers these types of places for consumption.

It is considered that the location within the neighborhood Narvarte Poniente is better because the category of venues in that area still does not exploit the specialized gourmet sites within the area, although if there are only two places of Seafood and Steakhouse but no precisely meet the specialized gourmet category sought by our client


### We can conclude that:
#1. The neighborhood analyzed is close to the most visited venues clusters
#2. In the Narvarte Poniente neighborhood there are only two business types similar to the client's objective
#3. There is no Gourmet business in the area, nor old meat, so it can be a neighborhood of opportunity to set up a business of this nature